**Rust Quantum Library**

*The Density Matrix*

The density matrix is a more general way of characterizing the overall state of a quantum system.  It is represented as $\rho = |\psi\rangle\langle\psi|$, where the wavefunction $|\psi\rangle$ is represented in Dirac notation as a column vector, and $\langle\psi|$ is the complex conjugate of the row vector. The density matrix can describe both pure states and mixed states. Pure states represent the state of one particle or the average state of an ensemble. In reality, most of the time mixed states are prepared or show up in nature. For example, light from the sun is a full mixture of quantum states, so it is not unpolarized and considered a maximally mixed state.

Here, we create density matrices out of the four Bell States, which are entangled quantum states:

$$\phi_- = \frac{1}{\sqrt{2}}(|00\rangle - |11\rangle)$$
$$\phi_+ = \frac{1}{\sqrt{2}}(|00\rangle + |11\rangle)$$
$$\psi_- = \frac{1}{\sqrt{2}}(|01\rangle - |10\rangle)$$
$$\psi_+ = \frac{1}{\sqrt{2}}(|01\rangle + |10\rangle)$$

In [50]:
:dep ndarray = { version = "0.14", features = ["serde"] }
:dep ndarray-linalg = { version = "0.13.1", features = ["intel-mkl-static"]}
:dep plotters = { git = "https://github.com/38/plotters", default_features = false, features = ["evcxr", "all_series"] }
:dep thiserror = "1.0"
:dep serde = { version = "1.0", features = ["derive"] }
:dep serde_json = "1.0"
:dep dimensioned = "0.7"
:dep num-complex = "0.4"

extern crate plotters;
use plotters::prelude::*;

extern crate ndarray;
use ndarray::prelude::*;
use ndarray_linalg::*;

let bell_phi_plus_coef: VecC64 = array![c64::new(norm_const , 0.0) , c64::new(0.0        , 0.0) , 
                                        c64::new(0.0        , 0.0) , c64::new(norm_const , 0.0) ];

let bell_phi_minus_coef: VecC64 = array![c64::new(norm_const , 0.0) , c64::new(0.0         , 0.0) , 
                                         c64::new(0.0        , 0.0) , c64::new(-norm_const , 0.0) ];

let bell_psi_plus_coef: VecC64 = array![c64::new(0.0        , 0.0) , c64::new(norm_const , 0.0) , 
                                        c64::new(norm_const , 0.0) , c64::new(0.0        , 0.0) ];

let bell_psi_minus_coef: VecC64 = array![c64::new(0.0         , 0.0) , c64::new(norm_const , 0.0) , 
                                        c64::new(-norm_const , 0.0) , c64::new(0.0        , 0.0) ];

pub fn create_dens_matrix(coefs: VecC64) -> MatrixC64 {

  let coefs_conj = coefs.map(|coefs| coefs.conj());
  let a = into_col(coefs);
  let b = into_row(coefs_conj);
  let dens_matrix = a.dot(&b);

  dens_matrix
}

println!("Density matrix for phi_+ = \n {:.1}", create_dens_matrix(bell_phi_plus_coef) );
println!("Density matrix for phi_- = \n {:.1}", create_dens_matrix(bell_phi_minus_coef) );
println!("Density matrix for psi_+ = \n {:.1}", create_dens_matrix(bell_psi_plus_coef) );
println!("Density matrix for psi_- = \n {:.1}", create_dens_matrix(bell_psi_minus_coef) );

Density matrix for phi_+ = 
 [[0.5+0.0i, 0.0+0.0i, 0.0+0.0i, 0.5+0.0i],
 [0.0+0.0i, 0.0+0.0i, 0.0+0.0i, 0.0+0.0i],
 [0.0+0.0i, 0.0+0.0i, 0.0+0.0i, 0.0+0.0i],
 [0.5+0.0i, 0.0+0.0i, 0.0+0.0i, 0.5+0.0i]]
Density matrix for phi_- = 
 [[0.5+0.0i, 0.0+0.0i, 0.0+0.0i, -0.5+0.0i],
 [0.0+0.0i, 0.0+0.0i, 0.0+0.0i, 0.0+0.0i],
 [0.0+0.0i, 0.0+0.0i, 0.0+0.0i, 0.0+0.0i],
 [-0.5+0.0i, 0.0+0.0i, 0.0+0.0i, 0.5+0.0i]]
Density matrix for psi_+ = 
 [[0.0+0.0i, 0.0+0.0i, 0.0+0.0i, 0.0+0.0i],
 [0.0+0.0i, 0.5+0.0i, 0.5+0.0i, 0.0+0.0i],
 [0.0+0.0i, 0.5+0.0i, 0.5+0.0i, 0.0+0.0i],
 [0.0+0.0i, 0.0+0.0i, 0.0+0.0i, 0.0+0.0i]]
Density matrix for psi_- = 
 [[0.0+0.0i, 0.0+0.0i, 0.0+0.0i, 0.0+0.0i],
 [0.0+0.0i, 0.5+0.0i, -0.5+0.0i, 0.0+0.0i],
 [0.0+0.0i, -0.5+0.0i, 0.5+0.0i, 0.0+0.0i],
 [0.0+0.0i, 0.0+0.0i, 0.0+0.0i, 0.0+0.0i]]


*Purity*

Purity is the trace of the square of the density matrix, $Tr(\rho^{2})$. In this example, we continuously add mixtures to a pure Bell state and graph its purity. The purity ranges from $\frac{1}{d}$ to 1, where $d$ is the dimension of the density matrix. In this case with a 4x4 density matrices, the purity ranges from 0.25 to 1.

In [3]:
:dep ndarray = { version = "0.14", features = ["serde"] }
:dep ndarray-linalg = { version = "0.13.1", features = ["intel-mkl-static"]}
:dep plotters = { git = "https://github.com/38/plotters", default_features = false, features = ["evcxr", "all_series"] }
:dep thiserror = "1.0"
:dep serde = { version = "1.0", features = ["derive"] }
:dep serde_json = "1.0"
:dep dimensioned = "0.7"
:dep num-complex = "0.4"

extern crate plotters;
use plotters::prelude::*;

extern crate ndarray;
use ndarray::prelude::*;
use ndarray_linalg::*;

pub use ndarray_linalg::c64;
pub type VecC64 = ndarray::Array1<c64>;
pub type VecF64 = ndarray::Array1<f64>;
pub type MatrixC64 = ndarray::Array2<c64>;
pub type MatrixF64 = ndarray::Array2<f64>;

pub fn create_dens_matrix(coefs: VecC64) -> MatrixC64 {

  let coefs_conj = coefs.map(|coefs| coefs.conj());
  let a = into_col(coefs);
  let b = into_row(coefs_conj);
  let dens_matrix = a.dot(&b);

  dens_matrix
}

pub fn find_purity(rho_sqrd: MatrixC64)-> f64 {
  let purity = rho_sqrd.trace().unwrap();
  purity.re
}

pub fn find_matrix_sqrd(matrix: MatrixC64) -> MatrixC64 {
  let matrix_sqrd = matrix.dot(&matrix); 
  matrix_sqrd
}

let norm_const: f64 = 1./2_f64.sqrt();

let bell_phi_plus_coef: VecC64 = array![c64::new(norm_const , 0.0) , c64::new(0.0        , 0.0) , 
                                        c64::new(0.0        , 0.0) , c64::new(norm_const , 0.0) ];

let bell_phi_minus_coef: VecC64 = array![c64::new(norm_const , 0.0) , c64::new(0.0         , 0.0) , 
                                         c64::new(0.0        , 0.0) , c64::new(-norm_const , 0.0) ];

let bell_psi_plus_coef: VecC64 = array![c64::new(0.0        , 0.0) , c64::new(norm_const , 0.0) , 
                                        c64::new(norm_const , 0.0) , c64::new(0.0        , 0.0) ];

let bell_psi_minus_coef: VecC64 = array![c64::new(0.0         , 0.0) , c64::new(norm_const , 0.0) , 
                                        c64::new(-norm_const , 0.0) , c64::new(0.0        , 0.0) ];

let mixed_state: MatrixC64 = array![ [  c64::new(0.25 , 0.) ,  c64::new(0. , 0.)  , c64::new(0. , 0.)  ,  c64::new(0. , 0.)  ] , 
                                  [  c64::new(0. , 0.) ,   c64::new(0.25 , 0.) , c64::new(0. , 0.)  ,  c64::new(0. , 0.)   ] ,
                                  [  c64::new(0. , 0.) ,   c64::new(0. , 0.)  , c64::new(0.25 , 0.) ,  c64::new(0. , 0.)   ] ,
                                  [  c64::new(0. , 0.) ,   c64::new(0. , 0.)  , c64::new(0. , 0.)  ,  c64::new(0.25 , 0.)   ] ];

/////////////////////////////////////////////////////////////////////////////////////////////////////////////////////////////////////

let mut points: Vec<(f64, f64)> = Vec::new();

for eta in 0..100{
    let a = c64::new((eta as f64)/100. , 0.);
    let b = c64::new(((100-eta) as f64)/100. , 0.);    
    let mut mixture = a*create_dens_matrix(bell_phi_plus_coef.clone()) + b*mixed_state.clone();
    let mut mixture_sqrd = find_matrix_sqrd(mixture);
    
    let mut purity = find_purity(mixture_sqrd);
    points.push( (eta as f64/100., purity) );
}

let figure = evcxr_figure((600, 400), |root| {
    root.fill(&WHITE);
    let mut chart = ChartBuilder::on(&root)
        .caption("Purity of mixed state and Bell state", ("Arial", 20).into_font())
        .margin(5)
        .x_label_area_size(30)
        .y_label_area_size(30)
        .build_cartesian_2d(0_f64..1_f64, 0_f64..1_f64)?;
    
    chart.configure_mesh().draw()?;
    chart.draw_series(points.into_iter().map(|(x,y)| Circle::new((x,y), 3, BLUE.filled())));
    Ok(())
});

figure

Purity of mixed state and Bell state
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
0.1
 
 
 
0.2
 
 
 
0.3
 
 
 
0.4
 
 
 
0.5
 
 
 
0.6
 
 
 
0.7
 
 
 
0.8
 
 
 
0.9
 
 
 
 
0.1
 
 
 
0.2
 
 
 
0.3
 
 
 
0.4
 
 
 
0.5
 
 
 
0.6
 
 
 
0.7
 
 
 
0.8
 
 
 
0.9
 
 
 
1.0

In [ ]:
*Concurrence*

In [56]:
:dep ndarray = { version = "0.14", features = ["serde"] }
:dep ndarray-linalg = { version = "0.13.1", features = ["intel-mkl-static"]}
:dep plotters = { git = "https://github.com/38/plotters", default_features = false, features = ["evcxr", "all_series"] }
:dep thiserror = "1.0"
:dep serde = { version = "1.0", features = ["derive"] }
:dep serde_json = "1.0"
:dep dimensioned = "0.7"
:dep num-complex = "0.4"

extern crate ndarray;
use ndarray::prelude::*;
use ndarray_linalg::*;

pub use ndarray_linalg::c64;
pub type VecC64 = ndarray::Array1<c64>;
pub type VecF64 = ndarray::Array1<f64>;
pub type MatrixC64 = ndarray::Array2<c64>;
pub type MatrixF64 = ndarray::Array2<f64>;


/////////////////////////////////////////////////////////////////////
/////////////////////////Matrix Operations///////////////////////////
/////////////////////////////////////////////////////////////////////

pub fn find_concurrence(rho: MatrixC64) -> f64 {
  
  let pauli_y = array![ [  c64::new(0. , 0.)  ,  c64::new(0. , 0.) , c64::new(0. , 0.) ,  c64::new(-1. , 0.)  ] , 
                        [  c64::new(0. , 0.)  ,  c64::new(0. , 0.) , c64::new(1. , 0.) ,  c64::new(0. , 0.)   ] ,
                        [  c64::new(0. , 0.)  ,  c64::new(1. , 0.) , c64::new(0. , 0.) ,  c64::new(0. , 0.)   ] ,
                        [  c64::new(-1. , 0.) ,  c64::new(0. , 0.) , c64::new(0. , 0.) ,  c64::new(0. , 0.)   ] ];

  let rho_star = rho.mapv(|rho| rho.conj());
  let sqrt_rho = find_sqr_root_of_matrix(rho.clone());
  let rho_tilde = pauli_y.dot(&rho_star).dot(&pauli_y);

  let product = sqrt_rho.dot(&rho_tilde).dot(&sqrt_rho);
  let sqrt_product = find_sqr_root_of_matrix(product);

  let (eigvals, _eigvecs) = sqrt_product.eigh(UPLO::Lower).unwrap();
  let mut eigvals = eigvals.to_vec();
  eigvals.sort_by(|a, b| a.partial_cmp(b).unwrap());
  0_f64.max(eigvals[3] - eigvals[2] - eigvals[1] - eigvals[0])
}

pub fn find_sqr_root_of_matrix(matrix: MatrixC64) -> MatrixC64 {
  
  let (matrix_d, matrix_s) = rescale_neg_eigvals(matrix);
  let matrix_s_inv = matrix_s.inv().unwrap();

  let sqrt_matrix_d = matrix_d.mapv(|matrix_d| (matrix_d).sqrt());

  let sqrt_product = matrix_s.dot(&sqrt_matrix_d).dot(&matrix_s_inv);
  sqrt_product
}

pub fn rescale_neg_eigvals(rho: MatrixC64) -> (MatrixC64, MatrixC64) {
  
  let (mut eigvals, vecs) = rho.eigh(UPLO::Lower).unwrap();
  let eig_len = eigvals.len() as i32;

  let mut j = 0;
  for _ctr in 0..eig_len {
    if eigvals[j] < 0.0 {
      eigvals[j] = 0.0;
  
      j += 1;
    }
  }

  let eigvals_c64 = eigvals.map(|f| c64::new(*f, 0.0));

  let matrix_d = MatrixC64::from_diag(&eigvals_c64);
  let matrix_s = vecs;

  (matrix_d, matrix_s)
}
///////////////////////////////////////////////////////////////////////////////////////////

extern crate plotters;
use plotters::prelude::*;
use core::f64::consts::PI;

let mut points: Vec<(f64, f64)> = Vec::new();
let mut points_x: Vec<f64> = Vec::new();
let mut points_y: Vec<f64> = Vec::new();

for i in 0..360{
    let mut theta: f64 = (i as f64)*PI/180.;
    let mut psi_part_entangled: VecC64 = array![c64::new(theta.cos(), 0.0), c64::new(0.0, 0.0), c64::new(0.0, 0.0), c64::new(theta.sin(), 0.0)];
    let mut rho_part_entangled: MatrixC64 = create_dens_matrix(psi_part_entangled);
    let mut concurrence: f64 = find_concurrence(rho_part_entangled);
    points.push( (theta, concurrence) );
    points_x.push(theta);
    points_y.push(concurrence);
}

let figure = evcxr_figure((600, 400), |root| {
    root.fill(&WHITE);
    let mut chart = ChartBuilder::on(&root)
        .caption("Concurrence of partially entangled state over theta", ("Arial", 20).into_font())
        .margin(5)
        .x_label_area_size(30)
        .y_label_area_size(30)
//         .x_desc("theta")
//         .y_desc("Concurrence")
        .build_cartesian_2d(0_f64..2.*PI, 0_f64..1_f64)?;
    
    chart.configure_mesh().draw()?;
    
    chart.draw_series(LineSeries::new(
        points_x.into_iter().zip(points_y.into_iter()), &RED,))?;

//     chart.configure_series_labels()
//         .background_style(&WHITE.mix(0.8))
//         .border_style(&BLACK)
//         .draw()?;
    Ok(())
});
figure

Concurrence of partially entangled state over theta
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
0.1
 
 
 
0.2
 
 
 
0.3
 
 
 
0.4
 
 
 
0.5
 
 
 
0.6
 
 
 
0.7
 
 
 
0.8
 
 
 
0.9
 
 
 
 
1.0
 
 
 
2.0
 
 
 
3.0
 
 
 
4.0
 
 
 
5.0
 
 
 
6.0
 
 
<polyline fill="none" opacity="1" stroke="#FF0000" stroke-width="1" points="35,364 36,352 38,340 39,329 41,317 42,306 44,294 45,283 47,271 49,260 50,249 52,238 53,228 55,217 56,207 58,197 59,187 61,177 63,167 64,158 66,149 67,140 69,131 70,123 72,115 73,108 75,100 77,93 78,87 80,80 81,74 83,69 84,63 86,58 87,54 89,50 91,46 92,42 94,39 95,37 97,35 98,33 100,31 101,31 103,31 105,31 106,31 108,31 109,31 111,33 112,35 114,37 115,39 117,42 119,46 120,50 122,54 123,58 125,63 126,69 128,74 129,80 131,87 133,93 134,100 136,108 137,115 139,123 140,131 142,140 143,149 145,158 147,167 148,177 150,187 151,197 153,207 154,217 156,228 157,238 159,249 161,260 162,271 164,283 165,294 167,306 168,317 170,329 171,340 173,352 175,364 176,352 178,340 179,329 181,317 182,306 184,294 185,283 187,271 189,260 190,249 192,238 193,228 195,217 196,207 198,197 199,187 201,177 203,167 204,158 206,149 207,140 209,131 210,123 212,115 213,108 215,100 217,93 218,87 220,80 221,74 223,69 224,63 226,58 227,54 229,50 231,46 232,42 234,39 235,37 237,35 238,33 240,31 241,31 243,31 245,31 246,31 248,31 249,31 251,33 252,35 254,37 255,39 257,42 259,46 260,50 262,54 263,58 265,63 266,69 268,74 269,80 271,87 273,93 274,100 276,108 277,115 279,123 280,131 282,140 283,149 285,158 287,167 288,177 290,187 291,197 293,207 294,217 296,228 297,238 299,249 301,260 302,271 304,283 305,294 307,306 308,317 310,329 311,340 313,352 315,364 316,352 318,340 319,329 321,317 322,306 324,294 325,283 327,271 329,260 330,249 332,238 333,228 335,217 336,207 338,197 339,187 341,177 343,167 344,158 346,149 347,140 349,131 350,123 352,115 353,108 355,100 357,93 358,87 360,80 361,74 363,69 364,63 366,58 367,54 369,50 371,46 372,42 374,39 375,37 377,35 378,33 380,31 381,31 383,31 385,31 386,31 388,31 389,31 391,33 392,35 394,37 395,39 397,42 399,46 400,50 402,54 403,58 405,63 406,69 408,74 409,80 411,87 413,93 414,100 416,108 417,115 419,123 420,131 422,140 423,149 425,158 427,167 428,177 430,187 431,197 433,207 434,217 436,228 437,238 439,249 441,260 442,271 444,283 445,294 447,306 448,317 450,329 451,340 453,352 455,364 456,352 458,340 459,329 461,317 462,306 464,294 465,283 467,271 469,260 470,249 472,238 473,228 475,217 476,207 478,197 479,187 481,177 483,167 484,158 486,149 487,140 489,131 490,123 492,115 493,108 495,100 497,93 498,87 500,80 501,74 503,69 504,63 506,58 507,54 509,50 511,46 512,42 514,39 515,37 517,35 518,33 520,31 521,31 523,31 525,31 526,31 528,31 529,31 531,33 532,35 534,37 535,39 537,42 539,46 540,50 542,54 543,58 545,63 546,69 548,74 549,80 551,87 553,93 554,100 556,108 557,115 559,123 560,131 562,140 563,149 565,158 567,167 568,177 570,187 571,197 573,207 574,217 576,228 577,238 579,249 581,260 582,271 584,283 585,294 587,306 588,317 590,329 591,340 593,352 "/>

In [58]:
:dep ndarray = { version = "0.14", features = ["serde"] }
:dep ndarray-linalg = { version = "0.13.1", features = ["intel-mkl-static"]}
:dep plotters = { git = "https://github.com/38/plotters", default_features = false, features = ["evcxr", "all_series"] }
:dep thiserror = "1.0"
:dep serde = { version = "1.0", features = ["derive"] }
:dep serde_json = "1.0"
:dep dimensioned = "0.7"
:dep num-complex = "0.4"

extern crate ndarray;
use ndarray::prelude::*;
use ndarray_linalg::*;

extern crate plotters;
use plotters::prelude::*;
use core::f64::consts::PI;

pub use ndarray_linalg::c64;
pub type VecC64 = ndarray::Array1<c64>;
pub type VecF64 = ndarray::Array1<f64>;
pub type MatrixC64 = ndarray::Array2<c64>;
pub type MatrixF64 = ndarray::Array2<f64>;


/////////////////////////////////////////////////////////////////////
/////////////////////////Matrix Operations///////////////////////////
/////////////////////////////////////////////////////////////////////

pub fn find_concurrence(rho: MatrixC64) -> f64 {
  
  let pauli_y = array![ [  c64::new(0. , 0.)  ,  c64::new(0. , 0.) , c64::new(0. , 0.) ,  c64::new(-1. , 0.)  ] , 
                        [  c64::new(0. , 0.)  ,  c64::new(0. , 0.) , c64::new(1. , 0.) ,  c64::new(0. , 0.)   ] ,
                        [  c64::new(0. , 0.)  ,  c64::new(1. , 0.) , c64::new(0. , 0.) ,  c64::new(0. , 0.)   ] ,
                        [  c64::new(-1. , 0.) ,  c64::new(0. , 0.) , c64::new(0. , 0.) ,  c64::new(0. , 0.)   ] ];

  let rho_star = rho.mapv(|rho| rho.conj());
  let sqrt_rho = find_sqr_root_of_matrix(rho.clone());
  let rho_tilde = pauli_y.dot(&rho_star).dot(&pauli_y);

  let product = sqrt_rho.dot(&rho_tilde).dot(&sqrt_rho);
  let sqrt_product = find_sqr_root_of_matrix(product);

  let (eigvals, _eigvecs) = sqrt_product.eigh(UPLO::Lower).unwrap();
  let mut eigvals = eigvals.to_vec();
  eigvals.sort_by(|a, b| a.partial_cmp(b).unwrap());
  0_f64.max(eigvals[3] - eigvals[2] - eigvals[1] - eigvals[0])
}

pub fn find_sqr_root_of_matrix(matrix: MatrixC64) -> MatrixC64 {
  
  let (matrix_d, matrix_s) = rescale_neg_eigvals(matrix);
  let matrix_s_inv = matrix_s.inv().unwrap();

  let sqrt_matrix_d = matrix_d.mapv(|matrix_d| (matrix_d).sqrt());

  let sqrt_product = matrix_s.dot(&sqrt_matrix_d).dot(&matrix_s_inv);
  sqrt_product
}

pub fn rescale_neg_eigvals(rho: MatrixC64) -> (MatrixC64, MatrixC64) {
  
  let (mut eigvals, vecs) = rho.eigh(UPLO::Lower).unwrap();
  let eig_len = eigvals.len() as i32;

  let mut j = 0;
  for _ctr in 0..eig_len {
    if eigvals[j] < 0.0 {
      eigvals[j] = 0.0;
  
      j += 1;
    }
  }

  let eigvals_c64 = eigvals.map(|f| c64::new(*f, 0.0));

  let matrix_d = MatrixC64::from_diag(&eigvals_c64);
  let matrix_s = vecs;

  (matrix_d, matrix_s)
}
///////////////////////////////////////////////////////////////////////////////////////////

let mut points: Vec<(f64, f64, f64)> = Vec::new();

let mixed_state: MatrixC64 = array![ [  c64::new(0.25 , 0.) ,  c64::new(0. , 0.)  , c64::new(0. , 0.)  ,  c64::new(0. , 0.)  ] , 
                                     [  c64::new(0. , 0.) ,   c64::new(0.25 , 0.) , c64::new(0. , 0.)  ,  c64::new(0. , 0.)   ] ,
                                     [  c64::new(0. , 0.) ,   c64::new(0. , 0.)  , c64::new(0.25 , 0.) ,  c64::new(0. , 0.)   ] ,
                                     [  c64::new(0. , 0.) ,   c64::new(0. , 0.)  , c64::new(0. , 0.)  ,  c64::new(0.25 , 0.)   ] ];

for eta_index in 0..100{
    let mut eta = c64::new((eta_index as f64)/100. , 0.);
  
    for theta_index in 0..360{
        let mut theta: f64 = (theta_index as f64)*PI/180.;
        let mut psi_part_entangled: VecC64 = array![c64::new(theta.cos(), 0.0), c64::new(0.0, 0.0), c64::new(0.0, 0.0), c64::new(theta.sin(), 0.0)];
        let mut rho_pure: MatrixC64 = create_dens_matrix(psi_part_entangled);
 
        let mut rho_mixed = eta*rho_pure.clone() + (1.-eta)*mixed_state.clone();
        let mut concurrence: f64 = find_concurrence(rho_mixed);
        points.push( (theta, eta.re, concurrence) ); 
    }

}


let figure = evcxr_figure((600, 400), |root| {
    root.fill(&WHITE);
    let mut chart = ChartBuilder::on(&root)
        .caption("Concurrence of mixed state and partially entangled state", ("Arial", 20).into_font())
        .margin(5)
        .x_label_area_size(30)
        .y_label_area_size(30)
        .build_cartesian_2d(0_f64..2.*PI, 0_f64..1_f64)?;
    
    chart.configure_mesh()
        .disable_x_mesh()
        .disable_y_mesh()
        .draw()?;
    

    chart.draw_series(
        points.into_iter()
               .map(|(theta, eta, concurrence)| {Rectangle::new(
                                                [ (theta, eta) , (theta + PI/18., eta + 0.1) ], 
                                                HSLColor(240.0 / 360.0 - 240.0 / 360.0 * (concurrence),
                                                         0.7,
                                                         0.1 + 0.4 * concurrence,
                                                        )
                                                
                                               .filled(),
                                                )}
                    )
    );
    
    
    Ok(())
});

figure

Concurrence of mixed state and partially entangled state
 
 
 
0.1
 
 
 
0.2
 
 
 
0.3
 
 
 
0.4
 
 
 
0.5
 
 
 
0.6
 
 
 
0.7
 
 
 
0.8
 
 
 
0.9
 
 
 
 
1.0
 
 
 
2.0
 
 
 
3.0
 
 
 
4.0
 
 
 
5.0
 
 
 
6.0
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 

*Fidelity*

This function is a distance measurement of two quantum states $\rho$ and $\sigma$. It is expressed as $F=tr\sqrt{\sqrt{\rho}\sigma\sqrt{\rho}}$.

In this example, the 2D rectangular plot shows $\theta$ on the x axis and $\eta$ on the y axis. The fidelity is plotted as a function of $\eta\rho_{pure} + (1-\eta)\rho_{mixed}$. The pure density matrix is a partially entangled state $\rho_{pure} = \sin\theta|00\rangle + \cos\theta|11\rangle$, and $\rho_{mixed} = 0.25I$ where $I$ is the 4x4 idenity matrix.

In [51]:
:dep ndarray = { version = "0.14", features = ["serde"] }
:dep ndarray-linalg = { version = "0.13.1", features = ["intel-mkl-static"]}
:dep plotters = { git = "https://github.com/38/plotters", default_features = false, features = ["evcxr", "all_series"] }
:dep thiserror = "1.0"
:dep serde = { version = "1.0", features = ["derive"] }
:dep serde_json = "1.0"
:dep dimensioned = "0.7"
:dep num-complex = "0.4"

extern crate ndarray;
use ndarray::prelude::*;
use ndarray_linalg::*;

extern crate plotters;
use plotters::prelude::*;
use core::f64::consts::PI;

pub use ndarray_linalg::c64;
pub type VecC64 = ndarray::Array1<c64>;
pub type VecF64 = ndarray::Array1<f64>;
pub type MatrixC64 = ndarray::Array2<c64>;
pub type MatrixF64 = ndarray::Array2<f64>;

pub fn create_dens_matrix(coefs: VecC64) -> MatrixC64 {

  let coefs_conj = coefs.map(|coefs| coefs.conj());
  let a = into_col(coefs);
  let b = into_row(coefs_conj);
  let dens_matrix = a.dot(&b);

  dens_matrix
}

pub fn find_fidelity(rho: MatrixC64, sigma: MatrixC64) -> f64 {

  let sqrt_rho = find_sqr_root_of_matrix(rho);
  let product = sqrt_rho.dot(&sigma).dot(&sqrt_rho);
  let sqrt_product = find_sqr_root_of_matrix(product);
  (sqrt_product.trace().unwrap()).re
}

pub fn find_sqr_root_of_matrix(matrix: MatrixC64) -> MatrixC64 {
  
  let (matrix_d, matrix_s) = rescale_neg_eigvals(matrix);
  let matrix_s_inv = matrix_s.inv().unwrap();

  let sqrt_matrix_d = matrix_d.mapv(|matrix_d| (matrix_d).sqrt());

  let sqrt_product = matrix_s.dot(&sqrt_matrix_d).dot(&matrix_s_inv);
  sqrt_product
}

pub fn rescale_neg_eigvals(rho: MatrixC64) -> (MatrixC64, MatrixC64) {
  
  let (mut eigvals, vecs) = rho.eigh(UPLO::Lower).unwrap();
  let eig_len = eigvals.len() as i32;

  let mut j = 0;
  for _ctr in 0..eig_len {
    if eigvals[j] < 0.0 {
      eigvals[j] = 0.0;
  
      j += 1;
    }
  }

  let eigvals_c64 = eigvals.map(|f| c64::new(*f, 0.0));

  let matrix_d = MatrixC64::from_diag(&eigvals_c64);
  let matrix_s = vecs;

  (matrix_d, matrix_s)
}

let mut points: Vec<(f64, f64, f64)> = Vec::new();

let mixed_state: MatrixC64 = array![ [  c64::new(0.25 , 0.) ,  c64::new(0. , 0.)  , c64::new(0. , 0.)  ,  c64::new(0. , 0.)  ] , 
                                     [  c64::new(0. , 0.) ,   c64::new(0.25 , 0.) , c64::new(0. , 0.)  ,  c64::new(0. , 0.)   ] ,
                                     [  c64::new(0. , 0.) ,   c64::new(0. , 0.)  , c64::new(0.25 , 0.) ,  c64::new(0. , 0.)   ] ,
                                     [  c64::new(0. , 0.) ,   c64::new(0. , 0.)  , c64::new(0. , 0.)  ,  c64::new(0.25 , 0.)   ] ];

for eta_index in 0..100{
    let mut eta = c64::new((eta_index as f64)/100. , 0.);
  
    for theta_index in 0..360{
        let mut theta: f64 = (theta_index as f64)*PI/180.;
        let mut psi_part_entangled: VecC64 = array![c64::new(theta.cos(), 0.0), c64::new(0.0, 0.0), c64::new(0.0, 0.0), c64::new(theta.sin(), 0.0)];
        let mut rho_pure: MatrixC64 = create_dens_matrix(psi_part_entangled);
 
        let mut rho_mixed = eta*rho_pure.clone() + (1.-eta)*mixed_state.clone();
        let mut fidelity: f64 = find_fidelity(rho_pure, rho_mixed);
        points.push( (theta, eta.re, fidelity) ); 
    }

}


let figure = evcxr_figure((600, 400), |root| {
    root.fill(&WHITE);
    let mut chart = ChartBuilder::on(&root)
        .caption("Fidelity of mixed state and partially entangled state", ("Arial", 20).into_font())
        .margin(5)
        .x_label_area_size(30)
        .y_label_area_size(30)
        .build_cartesian_2d(0_f64..2.*PI, 0_f64..1_f64)?;
    
    chart.configure_mesh()
        .disable_x_mesh()
        .disable_y_mesh()
        .draw()?;
    

    chart.draw_series(
        points.into_iter()
               .map(|(theta, eta, fidelity)| {Rectangle::new(
                                                [ (theta, eta) , (theta + PI/18., eta + 0.1) ], 
                                                HSLColor(240.0 / 360.0 - 240.0 / 360.0 * (fidelity),
                                                         0.7,
                                                         0.1 + 0.4 * fidelity,
                                                        )
                                                
                                               .filled(),
                                                )}
                    )
    );
    
    
    Ok(())
});

figure

Fidelity of mixed state and partially entangled state
 
 
 
0.1
 
 
 
0.2
 
 
 
0.3
 
 
 
0.4
 
 
 
0.5
 
 
 
0.6
 
 
 
0.7
 
 
 
0.8
 
 
 
0.9
 
 
 
 
1.0
 
 
 
2.0
 
 
 
3.0
 
 
 
4.0
 
 
 
5.0
 
 
 
6.0
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 


In [ ]:
*Negativity and Log Negativity*

In [54]:
:dep ndarray = { version = "0.14", features = ["serde"] }
:dep ndarray-linalg = { version = "0.13.1", features = ["intel-mkl-static"]}
:dep plotters = { git = "https://github.com/38/plotters", default_features = false, features = ["evcxr", "all_series"] }
:dep thiserror = "1.0"
:dep serde = { version = "1.0", features = ["derive"] }
:dep serde_json = "1.0"
:dep dimensioned = "0.7"
:dep num-complex = "0.4"

extern crate ndarray;
use ndarray::prelude::*;
use ndarray_linalg::*;

extern crate plotters;
use plotters::prelude::*;
use core::f64::consts::PI;

pub fn find_negativity(rho: MatrixC64) -> f64 {

  let trace_norm = find_trace_norm(rho);
  (trace_norm - 1.)/2.
}

pub fn find_trace_norm(rho: MatrixC64) -> f64 {

  let rho_partial_transpose = find_partial_transpose(rho);
  let rho_partial_transpose_star   = rho_partial_transpose.mapv(|rho_partial_transpose| rho_partial_transpose.conj());
  let rho_partial_transpose_dagger = rho_partial_transpose_star.t();
  
  let inner_product = (rho_partial_transpose_dagger).dot(&rho_partial_transpose);
  let partial_transpose_norm = find_sqr_root_of_matrix(inner_product); 
  let trace_norm =  partial_transpose_norm.trace().unwrap();
  trace_norm.re
}

pub fn find_log_negativity(rho: MatrixC64) -> f64 {
  let neg = find_negativity(rho);
  (2.*neg + 1.).log2()
}

pub fn find_dim(matrix: MatrixC64)-> i32 {
  let shape = matrix.dim();
  shape.1 as i32
}

pub fn find_partial_transpose(matrix: MatrixC64) -> MatrixC64 {

  let dim = find_dim(matrix.clone()) as usize;
  let mut partial_transpose_matrix = MatrixC64::zeros((dim , dim).f());

  let upper_left_block  = matrix.slice(s! [0..(dim / 2)   , 0..(dim / 2)  ] );
  let upper_right_block = matrix.slice(s! [0..(dim / 2)   , (dim / 2)..dim] );
  let lower_left_block  = matrix.slice(s! [(dim / 2)..dim , 0..(dim / 2)  ] );
  let lower_right_block = matrix.slice(s! [(dim / 2)..dim , (dim / 2)..dim] );

  let upper_right_block_transpose = upper_right_block.t();
  let lower_left_block_transpose = lower_left_block.t();

//TODO: Stack/concatenate
//Find for loops and see how to optimize
  let mut i = 0;
  for _index_1 in 0..dim/2 {
    let mut j = 0;
    for _index_2 in 0..dim/2 {
      partial_transpose_matrix[[i         , j        ]] = upper_left_block[ [i , j] ];
      partial_transpose_matrix[[i         , j + dim/2]] = upper_right_block_transpose[ [i , j] ];
      partial_transpose_matrix[[i + dim/2 , j        ]] = lower_left_block_transpose[ [i , j] ];
      partial_transpose_matrix[[i + dim/2 , j + dim/2]] = lower_right_block[ [i , j] ];
      j += 1;
      }
    i += 1;
    }

  partial_transpose_matrix

}

In [ ]:
pub fn find_schmidt_number(jsi: MatrixF64) -> f64 {
  let jsa = jsi.mapv(|jsi| jsi.sqrt());
  let (_u, s, _v_transpose) = jsa.svd(true , true).unwrap();
  let sum_eigvals_sqrd = s.mapv(|s| s*s).sum();
  let norm_const = 1./sum_eigvals_sqrd;
  let renormed_s = s.mapv(|s| s*(norm_const.sqrt()));
  let sum_eig_sqrd = renormed_s.mapv(|renormed_s| renormed_s.powf(4.)).sum();
  let k = 1./sum_eig_sqrd;
  k
}